## 0) Chiama i pacchetti e gli script necessari (step preliminare)

In [12]:
# Import needed packages
import numpy as np
import pandas as pd
#import datetime
import csv
import plotly.graph_objects as go

from SCRIPTS.Yearly_Calc import Yearly_Calculations as  Yearly_Calculations
from SCRIPTS.detailed_economic import Detailed_Economic_Analysis as  Detailed_Economic_Analysis
from SCRIPTS.utils import figure_scatter, figure_bar

# 1) Imposta gli input dell'analisi 
### I campi sottostanti sono gli unici campi da compilare se si vuole far girare il modello senza modificare niente
### Nota Bene: Vanno caricati i file .CSV nella cartella INPUT con i dati orari di producibilità fotovoltaica e i dati orari dei consumi
### Attenzione: usare i template csv forniti per caricare i dati (mantenere i nomi dei file e il nome delle colonne nel template CSV)

__modifiche__

[x] Creare un profilo orario di consumo delle famiglie, per mese, giorno della settimana

[ ] Creare un profilo di consumo orario dei negozi per mese e giorno della settimana

[x] Creare un profilo di autoconsumo orario della scuola per mese e giorno della settimana


[x] Consumo_famiglie <- consumo orario * numero di famiglie

[ ] Consumo_negozi <- consumo orario * numero di negozi

[x] Autoconsumo_scuola <- consumo orario * numero di scuole [mettere il totale e scuole=1]

[ ] Percentuale gratuità famiglie

[ ] Prezzo medio energia in CER?


In [13]:
import datetime
date_list = []
start_date = datetime.date(2022, 1, 1)
number_of_days = 365
for day in range(number_of_days):
  a_date = (start_date + datetime.timedelta(days = day)).isoformat()
  date_list.append(a_date)

In [14]:
profilo_consumo_famiglie_feriale=[0.0159236,0.0159236,0.0159236,0.0159236,0.0159236,0.0318471,0.0573248,0.0636943,0.0573248,0.0445860,
                         0.0445860,0.0445860,0.0445860,0.0445860,0.0445860,0.0445860,0.0573248,0.0573248,0.0636943,0.0636943,
                          0.0636943,0.0445860,0.0318471,0.0159236]
profilo_consumo_famiglie_festivo=[0.01510574,0.01510574,0.01510574,0.01510574,0.01510574,0.01510574,0.03021148,0.060422961,
                                  0.060422961,0.060422961,0.054380665,0.054380665,0.054380665,0.054380665,0.054380665,
                                  0.054380665,0.054380665,0.054380665,0.054380665,0.060422961,0.060422961,0.042296073,
                                  0.03021148,0.01510574]
# scuola: per la scuola è tutto rapportato al consumo medio feriale
numero_scuole=4
scuola_consumo_tot=26909*numero_scuole # in kWh
profilo_consumo_scuola_feriale=[1,1,1,1,5,10,10,10,10,10,10,10,10,10,7,7,7,7,5,1,1,1,1,1]
profilo_consumo_scuola_festivo=[1,1,1,1,2,2,2,2,2,2,2,2,2,2,2,2,2,2,2,1,1,1,1,1]
profilo_consumo_scuola_vacanza=[1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1]
# fc=fattore compensativo: questo fattore serve a rinormalizzare il consumo totale sul profilo di consumo
fc=scuola_consumo_tot/(sum(profilo_consumo_scuola_feriale)*193+sum(profilo_consumo_scuola_festivo)*78+
                       sum(profilo_consumo_scuola_vacanza)*94)

file_out='INPUT/Consumo_Carichi.csv'
dati=[]
numero_famiglie=50
consumo_annuo_famiglie=3000 #in kWh
consumo_giorno_famiglie=consumo_annuo_famiglie/365.
consumo_famiglie_tot=0
consumo_scuole_tot=0
feriale=1
festivo=1
vacanza=1
indice=1
for giorno in date_list:
    for i in range(0,24):
        #print (giorno,i)
        # consumo delle famiglie
        # feriale
        if pd.to_datetime(giorno).day_name() in ['Monday','Tuesday','Wednesday','Thursday','Friday']:
            consumo_h_famiglie=profilo_consumo_famiglie_feriale[i]*numero_famiglie*consumo_giorno_famiglie
        else:
        #festivo    
                consumo_h_famiglie=profilo_consumo_famiglie_festivo[i]*numero_famiglie*consumo_giorno_famiglie
        #print ( pd.to_datetime(giorno).day_name(), consumo_h_famiglie)
        #consumo delle scuole
        # testo se è feriale
        if giorno in ['2022-01-01','2022-01-02','2022-01-03', '2022-01-04','2022-01-05','2022-01-06','2022-04-14',
                     '2022-04-15','2022-04-16','2022-04-17', '2022-04-18', '2022-04-19','2022-04-20']:
            consumo_h_scuole=profilo_consumo_scuola_vacanza[i]*fc
            vacanza+=1
        elif indice> 3888 and indice <5833:
            consumo_h_scuole=profilo_consumo_scuola_vacanza[i]*fc
            vacanza+=1
        elif pd.to_datetime(giorno).day_name() in ['Monday','Tuesday','Wednesday','Thursday','Friday']:
            consumo_h_scuole=profilo_consumo_scuola_feriale[i]*fc
            feriale+=1
        elif pd.to_datetime(giorno).day_name() in ['Saturday', 'Sunday']:
            consumo_h_scuole=profilo_consumo_scuola_festivo[i]*fc
            festivo+=1
       
        consumo_famiglie_tot+=consumo_h_famiglie
        consumo_scuole_tot+=consumo_h_scuole
        #print (indice,consumo_h_famiglie+consumo_h_scuole)
        t=consumo_h_famiglie+consumo_h_scuole
        dati.append(t)
        indice+=1
    #print(giorno,pd.to_datetime(giorno).day_name(),indice,consumo_famiglie_tot,consumo_scuole_tot,feriale/24,festivo/24,vacanza/24)
    #p=pd.DataFrame({'Ora':list(range(1,8761)),'Consumo carichi, kWh':dati})
    

### 1 - 0) Scrivi il percorso del file contenente i dati sui consumi orari di tutti i membri della CER

questi due passaggi sono necessari per la scrittura su file

In [15]:
p=pd.DataFrame({'Ora':list(range(1,8761)),'Consumo carichi, kWh':dati})

In [16]:
p.to_csv('INPUT/Consumo_Carichi.csv', sep=';',index=False,decimal=',')

In [17]:
filename_Load ='INPUT/Consumo_Carichi.csv'

### 1 - 1) Taglia dell'impianto fotovoltaico (kWp) per cui sono stati inseriti i dati di producibilità oraria 

In [18]:
filename_FV ='INPUT/Produzione_FV.csv'
PV_kWp_dati = 50           #kWp

### 1 - 2) Taglia dell'impianto fotovoltaico (kWp) da simulare

In [41]:
PV_kWp = 140                #kWp

### 1 - 3) Dati di progetto della batteria

In [42]:
Capacity_Battery = 0.01                           # Capacità, kWh: non mettere 0 per overflow nelle divisioni
Maximum_Power = 0                                 # Potenza massima erogabile dalla batteria, kW
SOC_min = 5                                       # Stato di carica minimo, %
eta_BC = 0.99                                     # Efficienza di carica
eta_BD = 0.99                                     # Efficienza di scarica
SOC_0 = 50                                        # Stato di carica iniziale, %

### 1 - 4) Input economici

In [43]:
# Dati investimento - COSTO DI INVESTIMENTO SPECIFICO
CAPEX_PV_specifico = 1200         # eur/kWp
CAPEX_battery_specifico = 500     # eur/kWh

# Dati costi operativi (espressi in % dell'investimento)
OPEX_Perc = 3.5                    # %
Inverter  = 10                     # %

# Scegli la tipologia di schema
# Opzioni 'AC', 'CER'
Tipo = 'CER'                      #'CER' oppure 'AC'

# Dati incentivo (Lasciare invariato se si vuole rispettare la normativa attuale)
Incentivo_MISE     = 0.11  *(Tipo=='CER')  + 0.1*(Tipo=='AC')    # eur/kWh
Sgravio_ARERA      = 0.0075 *(Tipo=='CER')  + 0.01*(Tipo=='AC')   # eur/kWh

# Prezzo di mercato dell'energia elettrica
Prezzo_El_Mercato  = 0.12                                        # eur/kWh

# Tasso di attualizzazione - necessario per il calcolo del Valore Attuale Netto
Tasso_Attualizzazione = 5            # % 


# 2) Simulazione annuale

In [44]:
%run SCRIPTS/run_model.ipynb

%run SCRIPTS/define_figures.ipynb

Il carico annuale è di  257.6  MWh
La produzione FV annuale è di  172.8  MWh


# 3) Risultati

## 3.0 - Verifica il bilancio energetico

In [45]:
energy_balance

{'Conservazione Energia': 0.0,
 'Bilanci batteria': [0.0, 0.0045000000000000005]}

## 3.1) Consumi 

In [46]:
figure_consumption = figure_scatter(dict_plot_consumption,title_consumption, xlabel_consumption, ylabel_consumption)
figure_consumption.show()

figure_consumption2 = figure_bar(dict_plot_consumption2,title_consumption2, xlabel_consumption2, ylabel_consumption2)
figure_consumption2.show()

print('Il carico annuale è di ', round(df_hourly['Consumo carichi, kWh'].sum()/1e3,1), ' MWh')

Il carico annuale è di  257.6  MWh


## 3.2 - Produzione fotovoltaico

In [47]:
figure_PV1 = figure_scatter(dict_plot_PV1,title_PV1, xlabel_PV1, ylabel_PV1)
figure_PV1.show()

figure_PV2 = figure_bar(dict_plot_PV2,title_PV2, xlabel_PV2, ylabel_PV2)
figure_PV2.show()

print('La produzione annuale di un impianto da ' ,str(PV_kWp) , ' kWp risulta uguale a  ', 
      round(df_hourly['Produzione PV, kWh'].sum()/1000,2), ' MWh')
print('Le ore equivalenti sono ', 
      round(df_hourly['Produzione PV, kWh'].sum()/PV_kWp,2))

La produzione annuale di un impianto da  140  kWp risulta uguale a   172.85  MWh
Le ore equivalenti sono  1234.63


## 3.3- Flussi energetici orari annuali

In [48]:
figure_energyflux = figure_scatter(dict_plot_energyflux,title_energyflux, xlabel_energyflux, ylabel_energyflux)
figure_energyflux.show()



figure_monthly_overall = figure_bar(dict_plot_monthly_overall,title_monthly_overall, xlabel_monthly_overall, ylabel_monthly_overall)
figure_monthly_overall.show()



figure_monthly_overall2 = figure_bar(dict_plot_monthly_overall2,title_monthly_overall2, xlabel_monthly_overall2, 
                                     ylabel_monthly_overall2)
figure_monthly_overall2.show()


## 3.4 - Analisi del funzionamento della batteria

In [49]:
figure_battery = figure_scatter(dict_plot_battery,title_battery, xlabel_battery, ylabel_battery)

if economy_output['Cicli batteria']>0:
    figure_battery.show()
    try:
        print('In un anno di funzionamento, la batteria subisce ', int(economy_output['Cicli batteria']), ' cicli di carica/scarica')
    except:
        print('Nessuna batteria installata')
else:
    print('Cicli batteria nulli')

Cicli batteria nulli


In [50]:
economy_output['Cicli batteria']

0.0

# 4) Risultati: analisi economica

## 4.0) Investimento - Costi operativi e Ricavi

In [51]:
print('Investimento fotovoltaico, eur', round(economy_output['CAPEX_PV'],0))
print('Investimento accumulo, eur', round(economy_output['CAPEX_battery'] ,0))
print('Investimento totale, eur', round(economy_output['CAPEX_battery']+economy_output['CAPEX_PV'] ,0))
print('Costi operativi, eur/anno', round(economy_output['OPEX'] ,0))
print('Costi riampiazzo inverter (anno 10), eur', round(economy_output['InverterCost'] ,0))

print()

print('Totale energia condivisa PV, kWh ', round(economy_output['Energia_Condivisa_PV'],0))
print('Totale energia condivisa batteria, kWh ', round(economy_output['Energia_Condivisa_Batteria'],0))
print('Totale energia condivisa, kWh ', round(economy_output['Energia_Condivisa'],0))
print()
print('% energia condivisa ', round(economy_output['Energia_Condivisa']/economy_output['Energia_Consumi']*100), ' %')
print('% energia condivisa Fotovoltaico ', round(economy_output['Energia_Condivisa_PV']/economy_output['Energia_Consumi']*100), ' %')
print('% energia condivisa Batteria ', round(economy_output['Energia_Condivisa_Batteria']/economy_output['Energia_Consumi']*100), ' %')
print()
print('Totale energia consumata, kWh ', round(economy_output['Energia_Consumi'],0))
print('Totale energia immessa in rete (totale), kWh ', round(economy_output['Energia_Immessa_In_Rete'],0))
print('Totale energia prelevata dalla rete (totale), kWh ', round(economy_output['Energia_Prelevata_tot'],0))
print()


print('Incentivo MISE, eur/anno ', round(economy_output['Ritorno_MISE'],0))
print('Sgravio ARERA, eur/anno ', round(economy_output['Ritorno_ARERA'],0))
print('Vendita energia elettrica, eur/anno ', round(economy_output['Ritorno_RID'],0))
print('Totale ricavi, eur/anno ', round(economy_output['Totale_Ricavi'],0))


Investimento fotovoltaico, eur 168000
Investimento accumulo, eur 5.0
Investimento totale, eur 168005.0
Costi operativi, eur/anno 5880.0
Costi riampiazzo inverter (anno 10), eur 16800.0

Totale energia condivisa PV, kWh  114084.0
Totale energia condivisa batteria, kWh  0.0
Totale energia condivisa, kWh  114084.0

% energia condivisa  44  %
% energia condivisa Fotovoltaico  44  %
% energia condivisa Batteria  0  %

Totale energia consumata, kWh  257636.0
Totale energia immessa in rete (totale), kWh  172849.0
Totale energia prelevata dalla rete (totale), kWh  257636.0

Incentivo MISE, eur/anno  12549.0
Sgravio ARERA, eur/anno  856.0
Vendita energia elettrica, eur/anno  20742.0
Totale ricavi, eur/anno  34147.0


## 4.1 ) Tempo di ritorno dell'investimento e Valore Attuale Netto a 20 anni
NB. Le due curve mostrano lo scenario in cui sono applicate le detrazioni fiscali sul 50 % dell'investimento (per un max investimento di 96.000 EUR) spalmate sui primi 10 anni, e lo scenario in cui nessuna detrazione è applicata

In [39]:
figure_VAN = figure_scatter(dict_VAN,title_VAN, xlabel_VAN, ylabel_VAN)
figure_VAN.show()

PBT_1 =  np.round(((economy_output['CAPEX_PV']+economy_output['CAPEX_battery'])/(economy_output['Totale_Ricavi']-economy_output['OPEX'])),1)
PBT_detrazioni = np.round(((economy_output['CAPEX_PV']+economy_output['CAPEX_battery'])/(economy_output['Totale_Ricavi']-economy_output['OPEX'] + min((economy_output['CAPEX_PV']+economy_output['CAPEX_battery']), 96000)/10*0.5)),1)
print()
print('Tempo ritorno dell investimento ', PBT_1 , ' anni')
print('Tempo ritorno dell investimento (detrazioni 50 %)',PBT_detrazioni , ' anni')



Tempo ritorno dell investimento  5.4  anni
Tempo ritorno dell investimento (detrazioni 50 %) 4.5  anni


## 5) Esporta i risultati in un file CSV

In [207]:
# Scegli il nome del file in cui salvare i risultati
filename_output = 'OUTPUT/OutputSimulazione.csv'

In [208]:
OUTPUT_DICTIONARY = {'Taglia FV kWp': PV_kWp, 
                     'Taglia batteria kWh': Capacity_Battery, 
                     'Consumi annuali kWh/anno': economy_output['Energia_Consumi'],
                     'Investimento FV EUR': economy_output['CAPEX_PV'],
                     'Investimento accumulo EUR': economy_output['CAPEX_battery'],
                     'Costi operativi EUR/anno': economy_output['OPEX'],
                     'Costi riampiazzo inverter EUR/anno': economy_output['InverterCost'],
                     'Energia condivisa FV kWh/anno': economy_output['Energia_Condivisa_PV'],
                     'Energia condivisa batteria kWh/anno': economy_output['Energia_Condivisa_Batteria'],
                     'Totale energia immessa in rete kWh/anno': economy_output['Energia_Immessa_In_Rete'],
                     'Totale energia prelevata dalla rete kWh/anno': economy_output['Energia_Prelevata_tot'],
                     'Ricavo MISE EUR/anno':economy_output['Ritorno_MISE'],
                     'Sgravio ARERA EUR/anno':economy_output['Ritorno_ARERA'],
                     'Vendita energia elettrica EUR/anno': economy_output['Ritorno_RID'],
                     'Tempo di ritorno senza detrazioni': PBT_1,
                     'Tempo di ritorno con detrazioni': PBT_detrazioni,
                    }

df_OUTPUT = pd.DataFrame.from_dict(OUTPUT_DICTIONARY,orient='index')
df_OUTPUT.to_csv(filename_output, decimal =',', sep=';')

In [18]:
economy_output['Cicli batteria']

0

In [40]:
economy_output

{'Capacity_Battery': 0.01,
 'CAPEX_battery_specifico': 500,
 'PV_kWp': 100,
 'Energia_Prodotta_PV': 123463.22745442402,
 'Energia_Scarica_Batteria': 0.0,
 'Energia_Ricarica_Batteria': 0.0,
 'Energia_Prelevata_Extra': 159895.15824872922,
 'Energia_Prelevata_tot': 257636.0214993151,
 'Energia_Immessa_In_Rete_extra': 25722.36420383813,
 'Energia_Consumi': 257636.0214993151,
 'Energia_Condivisa_PV': 97740.86325058585,
 'Energia_Condivisa_Batteria': 0.0,
 'Energia_Condivisa': 97740.86325058585,
 'Energia_Immessa_In_Rete': 123463.22745442402,
 'Ritorno_MISE': 10751.494957564444,
 'Ritorno_ARERA': 733.0564743793939,
 'Ritorno_RID': 14815.587294530882,
 'Totale_Ricavi': 26300.138726474717,
 'Perc_EnergiaCondivisa': 37.93757669513061,
 'Perc_EnergiaCondivisa_PV': 37.93757669513061,
 'Perc_EnergiaCondivisa_Batteria': 0.0,
 'CAPEX_PV': 120000,
 'CAPEX_battery': 5.0,
 'OPEX': 4200.0,
 'InverterCost': 12000.0,
 'Cicli batteria': 0.0}